In [ ]:
#  Copyright 2016 The TensorFlow Authors. All Rights Reserved.
#
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#
#   http://www.apache.org/licenses/LICENSE-2.0
#
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.
"""Convolutional Neural Network Estimator for MNIST, built with tf.layers."""

In [9]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf
from tensorflow import keras

tf.logging.set_verbosity(tf.logging.INFO)

In [2]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [12]:
(train_data, train_labelseval_data), (eval_data, eval_labels)= keras.datasets.mnist.load_data()

((array([[[0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          ...,
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0]],
  
         [[0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          ...,
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0]],
  
         [[0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          ...,
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0]],
  
         ...,
  
         [[0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          ...,
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0]],
  
         [[0, 0, 0, ..., 0, 0, 0],
          [0, 0, 0, ..., 0, 0, 0

In [21]:
train_data.shape

(55000, 784)

In [20]:
keras.datasets.mnist.load_data()[0][0].shape

(60000, 28, 28)

In [3]:
# Load training and eval data
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images  # Returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images  # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

# Create the Estimator
mnist_classifier = tf.estimator.Estimator(
  model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

# Set up logging for predictions
# Log the values in the "Softmax" tensor with label "probabilities"
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(
  tensors=tensors_to_log, every_n_iter=50)

# Train the model
train_input_fn = tf.estimator.inputs.numpy_input_fn(
  x={"x": train_data},
  y=train_labels,
  batch_size=100,
  num_epochs=None,
  shuffle=True)
mnist_classifier.train(
  input_fn=train_input_fn,
  steps=20000,
  hooks=[logging_hook])

# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
  x={"x": eval_data},
  y=eval_labels,
  num_epochs=1,
  shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

Instructions for updating:
Please use tf.data.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use urllib or similar directly.
Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-u

INFO:tensorflow:loss = 2.336951, step = 0
INFO:tensorflow:probabilities = [[0.08874682 0.10707946 0.11991311 0.09222518 0.1023589  0.10082287
  0.09606248 0.09909727 0.10363288 0.09006106]
 [0.09489222 0.09892552 0.11888536 0.08268909 0.0963124  0.1140653
  0.09887651 0.09609319 0.10950699 0.08975337]
 [0.08759277 0.12426011 0.1259529  0.08765322 0.09145263 0.09027347
  0.11005922 0.08781032 0.10990253 0.08504289]
 [0.08601773 0.1019837  0.11472781 0.09349547 0.0941072  0.10239285
  0.10632569 0.10041981 0.1153338  0.08519592]
 [0.09853455 0.10181607 0.11147675 0.09059    0.1022827  0.09298953
  0.09042472 0.09772304 0.12261663 0.091546  ]
 [0.10229059 0.10316864 0.1267384  0.087345   0.0924175  0.09366438
  0.09637778 0.09257849 0.11251552 0.09290368]
 [0.09152872 0.10676692 0.11660898 0.10158084 0.10128195 0.09829183
  0.10224929 0.08795943 0.10718041 0.08655169]
 [0.09116296 0.12057049 0.10848033 0.09115921 0.09528736 0.08744262
  0.09917997 0.09030249 0.13272427 0.08369029]
 [0.090

INFO:tensorflow:global_step/sec: 61.2234
INFO:tensorflow:probabilities = [[0.08867806 0.11046337 0.11974145 0.10182838 0.09647805 0.09604349
  0.10382669 0.09531119 0.10089278 0.08673656]
 [0.0804434  0.13016365 0.11648671 0.10091276 0.09654289 0.09130973
  0.10179719 0.0864763  0.10941121 0.08645611]
 [0.09666133 0.11567777 0.11198956 0.10303698 0.10514958 0.08884758
  0.09426262 0.09079367 0.10291407 0.09066684]
 [0.09144698 0.10391597 0.11451828 0.109755   0.09660514 0.10218693
  0.1030542  0.0848936  0.11745781 0.07616606]
 [0.0964816  0.09937208 0.11312927 0.10500773 0.09432763 0.09407129
  0.10550147 0.08524338 0.12144857 0.08541709]
 [0.09933897 0.10485016 0.10182407 0.09494727 0.1013267  0.09896337
  0.09773349 0.09820462 0.10716394 0.09564745]
 [0.09011357 0.11302221 0.10666483 0.10547548 0.1005602  0.10392784
  0.09688935 0.10406353 0.09619038 0.08309269]
 [0.08488717 0.10857155 0.10645545 0.09748719 0.09341777 0.10512015
  0.10941158 0.09732921 0.10881016 0.08850977]
 [0.095

INFO:tensorflow:loss = 2.277878, step = 100 (1.633 sec)
INFO:tensorflow:probabilities = [[0.09076015 0.12041182 0.11344127 0.10355593 0.09561231 0.09644651
  0.09978168 0.08914436 0.10603114 0.0848148 ]
 [0.1017823  0.10355616 0.10084446 0.09642225 0.09905897 0.10018437
  0.1050582  0.09745581 0.09959012 0.09604736]
 [0.09351676 0.10350189 0.11134362 0.10134449 0.10909976 0.09323242
  0.09551159 0.08759104 0.10912271 0.09573568]
 [0.09859978 0.10681431 0.10264255 0.09019388 0.08666947 0.09819087
  0.09453185 0.1086309  0.11381163 0.0999148 ]
 [0.10558397 0.09487431 0.11062616 0.10333264 0.08989397 0.09514853
  0.11346693 0.08622004 0.11090726 0.08994623]
 [0.09359997 0.10076839 0.11092477 0.09263346 0.09803616 0.10918783
  0.10812344 0.0941423  0.10130586 0.09127789]
 [0.09973361 0.10415032 0.11309528 0.1031354  0.09458589 0.09324133
  0.08375227 0.10664549 0.10915637 0.09250404]
 [0.09449741 0.10921384 0.10641618 0.10035204 0.09506169 0.09701939
  0.09883663 0.0896534  0.10631491 0.10

INFO:tensorflow:global_step/sec: 66.6942
INFO:tensorflow:probabilities = [[0.09202959 0.10412228 0.10114139 0.10255208 0.10447174 0.09132866
  0.10648744 0.08802158 0.11344907 0.09639617]
 [0.09153694 0.10681823 0.11500861 0.09212792 0.09515746 0.09598779
  0.10682357 0.09100312 0.11142629 0.09411007]
 [0.09274904 0.09533165 0.11568097 0.09638673 0.10930713 0.09629467
  0.08569481 0.08817223 0.12340307 0.09697963]
 [0.0973629  0.10359218 0.11865385 0.0998334  0.09866771 0.09052022
  0.11032902 0.08842925 0.10489567 0.0877158 ]
 [0.08820201 0.10672455 0.11619134 0.09262076 0.10741999 0.10310145
  0.10816438 0.08825877 0.10593171 0.08338512]
 [0.09465335 0.10007806 0.12787037 0.08465954 0.0958094  0.10427333
  0.10934637 0.09322562 0.10508326 0.08500073]
 [0.09162778 0.09599586 0.11204898 0.0977896  0.092508   0.10871226
  0.09941976 0.10570048 0.10409405 0.09210323]
 [0.09367549 0.09868515 0.09881451 0.09195267 0.09802831 0.09810047
  0.10964345 0.09804579 0.12125285 0.09180135]
 [0.091

...

INFO:tensorflow:global_step/sec: 55.3203
INFO:tensorflow:probabilities = [[0.00266178 0.01209903 0.03004099 0.05482929 0.01465903 0.00617058
  0.00144567 0.00344952 0.86494046 0.00970372]
 [0.00000021 0.00000056 0.00003854 0.0000187  0.9991358  0.00055246
  0.00017509 0.00000355 0.00004978 0.00002536]
 [0.00001991 0.9868166  0.00320146 0.00214027 0.00177397 0.00147285
  0.0005234  0.00039285 0.00364671 0.00001205]
 [0.00000793 0.00000159 0.00006707 0.00000015 0.00031589 0.00005384
  0.99951994 0.00000064 0.0000323  0.00000074]
 [0.00269129 0.0012695  0.00111684 0.00796169 0.79225713 0.00568429
  0.00018849 0.0660165  0.00018771 0.12262655]
 [0.00208058 0.00020969 0.00004424 0.0024259  0.00000007 0.99376655
  0.00001013 0.00038188 0.00098807 0.00009276]
 [0.00003982 0.00000213 0.00043322 0.00000255 0.00002886 0.00005253
  0.999383   0.00000018 0.00005607 0.00000163]
 [0.00024743 0.00011098 0.00093919 0.00101942 0.00026872 0.00183335
  0.00137653 0.00003946 0.9926669  0.00149795]
 [0.009

INFO:tensorflow:loss = 0.18152733, step = 19800 (1.752 sec)
INFO:tensorflow:probabilities = [[0.00009981 0.99702865 0.00022596 0.00004656 0.00001228 0.0000244
  0.00019554 0.00030515 0.00202164 0.00003998]
 [0.00000607 0.00000489 0.00002421 0.00024769 0.00002027 0.9944389
  0.00184741 0.00000055 0.00315946 0.00025053]
 [0.00018778 0.00003113 0.00004601 0.00002246 0.0001579  0.9989513
  0.00046875 0.0000404  0.00009274 0.00000142]
 [0.00000021 0.00000413 0.00000215 0.99994445 0.         0.00000545
  0.         0.00000143 0.00003096 0.00001127]
 [0.0000005  0.00000001 0.00001156 0.00003791 0.         0.00000006
  0.         0.99979347 0.00000011 0.00015632]
 [0.08132479 0.0000463  0.19640422 0.00021003 0.00141124 0.1601176
  0.52684224 0.00001479 0.03284156 0.00078715]
 [0.00000613 0.0000025  0.9996432  0.00032193 0.0000002  0.
  0.0000001  0.00000025 0.00002542 0.00000018]
 [0.0000003  0.00004351 0.00000274 0.998187   0.00000002 0.00166806
  0.0000003  0.00000561 0.00007538 0.00001709]


INFO:tensorflow:global_step/sec: 63.1654
INFO:tensorflow:probabilities = [[0.9999852  0.00000012 0.00001223 0.00000031 0.         0.00000169
  0.00000001 0.00000009 0.00000004 0.00000028]
 [0.00000038 0.00000029 0.00000709 0.00009539 0.00135703 0.00002907
  0.00000014 0.04444361 0.00035881 0.9537082 ]
 [0.00129902 0.00472942 0.001387   0.00087057 0.00195278 0.97353137
  0.00757646 0.00154487 0.00686286 0.00024571]
 [0.00002781 0.00040412 0.00007192 0.00183054 0.00877914 0.00057504
  0.00002653 0.00073422 0.00497402 0.98257667]
 [0.00003628 0.01767386 0.00295069 0.0258215  0.00003865 0.00000361
  0.00000131 0.93992436 0.00142514 0.01212451]
 [0.00011978 0.00005403 0.00055156 0.00002376 0.1203193  0.00266395
  0.00066934 0.00080488 0.30497506 0.5698184 ]
 [0.00001538 0.99763834 0.00040464 0.00014072 0.00011154 0.00005639
  0.00017246 0.00005488 0.0013331  0.00007256]
 [0.00000884 0.99785835 0.00008688 0.00094595 0.00010367 0.00001506
  0.00004353 0.00040705 0.00032995 0.00020071]
 [0.000

INFO:tensorflow:loss = 0.24967135, step = 19900 (1.576 sec)
INFO:tensorflow:probabilities = [[0.9999689  0.00000001 0.00000499 0.0000001  0.00000002 0.00000663
  0.00000578 0.00000019 0.00000811 0.00000519]
 [0.0000525  0.9987043  0.00011958 0.00024502 0.00006742 0.00000451
  0.00002537 0.00047341 0.00024048 0.00006723]
 [0.9978478  0.00000011 0.00102757 0.00001167 0.00000001 0.0011068
  0.00000324 0.00000042 0.00000076 0.00000166]
 [0.9990877  0.0000007  0.00055176 0.0000696  0.00000001 0.0001569
  0.00000482 0.00000153 0.00000052 0.00012649]
 [0.00070761 0.9915639  0.00512775 0.0004448  0.00023677 0.00003774
  0.00016835 0.0008404  0.00070179 0.00017095]
 [0.00023524 0.00000344 0.00005642 0.00008808 0.00000013 0.998884
  0.00001362 0.00000011 0.00071745 0.00000158]
 [0.00093883 0.0000316  0.00018931 0.0000137  0.00115879 0.00097236
  0.9961132  0.00000128 0.00044852 0.00013235]
 [0.00000395 0.00000085 0.00000254 0.00111047 0.00000029 0.9985373
  0.00001582 0.00000009 0.00000545 0.000

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.21221328.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-07-09-12:14:50
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-07-09-12:14:51
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.969, global_step = 20000, loss = 0.10378289
{'accuracy': 0.969, 'loss': 0.10378289, 'global_step': 20000}
